<a class="anchor" id="import"></a>
# Imports and setup

Please note that this notebook is written for Python 3.

In [455]:
# 3rd party
import numpy as np
from astropy.table import Table
from astropy.cosmology import Planck18 as cosmo
import plotly
import plotly.graph_objs as go
plotly.offline.init_notebook_mode()

# Data Lab
from dl import queryClient as qc

<a class="anchor" id="3d_plot"></a>
# Interactive 3D plot (RA, DEC and z)

We now turn to a different area of the sky. We want to identify filaments and clumps of galaxies in 3D, moving around and 'traveling' through space.

We want to take an interesting section of the sky, where we could observe galaxies clustering and/or filaments of the large scale structure of the universe, as we did in the previous section, except that now we can move through 'space' within those galaxies and see them from different points of view in that section of the universe.

We chose an are far from the galactic plane of the Milky Way

Next, we will get the SDSS data for positions and redshifts, and define our boundaries.

In [456]:
#Create the query to fetch the SDSS data from DataLab:
#query = """
#SELECT ra,dec,z
#FROM sdss_dr17.specobj
#WHERE ra BETWEEN %s AND %s
#AND dec BETWEEN %s AND %s
#AND z between %s AND %s""" 
#% (160,220,0,6,0.02,.4)
#print (query)

query = """
SELECT ra,dec,z
FROM sdss_dr17.specobj
WHERE q3c_radial_query(ra,dec,%s,%s,%s)
""" % (190,3,10)
print (query)


SELECT ra,dec,z
FROM sdss_dr17.specobj
WHERE q3c_radial_query(ra,dec,190,3,10)



In [457]:
%%time
# Fetch the SDSS data from ls_dr17.specobj
selection = qc.query(adql=query, fmt='csv')

CPU times: user 72 ms, sys: 17.7 ms, total: 89.7 ms
Wall time: 1.74 s


In [458]:
# Reformat output into a table
data = Table.read(selection, format='csv')  #dictionary

In [459]:

#ra = data['ra'].value
#dec = data['dec'].value
#z = data['z'].value

ra = data['ra']
dec = data['dec']
z = data['z']

ra_ = ra
dec_ = dec
z_ = z
print('There initially are %s points to plot'%len(ra_))

sel = (ra_ > 180) & (ra_ < 195) & (dec_ > 5) & (dec_ < 20) & (z_ > 0.02) & (z_ < 0.4)
#sel = (ra > 180) & (ra < 195) & (dec > 5) & (dec < 20) & (z > 0.02) & (z < 0.4)
ra_ = ra_[sel]
dec_ = dec_[sel]
z_ = z_[sel]
#ra,dec,z

print('Now here are %s points to plot'%len(ra_))

There initially are 100867 points to plot
Now here are 12678 points to plot


Compute luminosity distance for every galaxy, using Planck cosmology values

In [460]:
#dist = cosmo.luminosity_distance(z)
dist = cosmo.luminosity_distance(z_)
dist

<Quantity [ 637.8475169 ,  760.91369067,  366.84218912, ...,  764.05768742,
           1045.1909696 , 2106.89467155] Mpc>

Get rid of a few local galaxies with negative distances

In [461]:
dist.min()

<Quantity 91.27540214 Mpc>

In [462]:
#sel = (dist>0) 

ra = ra_
dec = dec_

In [463]:
print('There are %s points to plot'%len(ra))

There are 12678 points to plot


In [464]:
dist.min()

<Quantity 91.27540214 Mpc>

Convert ra,dec,dist to cartesian coordinates X,Y,Z (in Mpc)

In [465]:
def get_cartesian(ra,dec,dist):
    rarad = np.radians(ra)
    decrad = np.radians(dec)
    X = dist * np.sin(decrad) * np.cos(rarad)
    Y = dist * np.sin(decrad) * np.sin(rarad)
    Z = dist * np.cos(decrad)
    return X,Y,Z

In [466]:
X,Y,Z = get_cartesian(ra,dec,dist)

### Plotting in 3D
We want to take an interesting section of the sky, where we could observe galaxies clustering and/or filaments of the large scale structure of the universe, as we did in the previous section, EXCEPT, that now we can move through 'space' within those galaxies and see them from different points of view in that section of the universe.

In the following cell, we will get the SDSS data for coordinates and redshift, and define our boundaries:

Now we prepare the trace to plot

In [467]:
trace = go.Scatter3d(
    x = X,
    y = Y,
    z = -Z,
    mode = 'markers',
    marker = {
        'size'      : 1.5,
        'opacity'   : 0.7,
        'color'     : dist, 
        'colorscale': 'OrRd'
    }
)

In [468]:
data = [trace]

Next, we define camera location and the layout of the plot

In [469]:
camera = dict(
    up = dict(x = 0, y = 0, z = 1),
    center = dict(x = 0, y = 0, z = 0),
    eye = dict(x = -0.2, y = -0.2, z = -1)
)

layout = go.Layout(
    scene = dict(
        xaxis = dict(title = 'X',
                     backgroundcolor = 'black',
                     showbackground=True,
                     gridcolor = "black",
                     ),
        yaxis = dict(title = 'Y',
                     backgroundcolor = 'black',
                     showbackground=True,
                     gridcolor = "black",
                     ),
        zaxis = dict(title = 'Z',
                     backgroundcolor = 'black',
                     showbackground=True,
                     gridcolor = "black",
                     ),
    ),
        scene_camera = camera,
        plot_bgcolor = 'black',
        paper_bgcolor = 'black',
        title = None,
        showlegend=False,
        width = 1000,
        height = 1000,
        autosize = False,
        margin = {'l':0, 'r':0, 'b':0, 't':0}
)

In [470]:
# Now we finally draw the plot:
plot_figure = go.Figure(data = data, layout = layout)
plot_figure.update_layout()
#plot_figure.update_scenes(
     #camera_eye_x = 0.4,
     #camera_eye_y = 0.4,
     #camera_eye_z = 0.13,
     #camera_eye_x = 1.25,
     #camera_eye_y = 1.25,
     #camera_eye_z = -1.25,
    #)